## COLAB NOTEBOOK FOR THE AZURE CST RESULTS EVALUATIONS

In [2]:
!pip install --upgrade pip
!pip install unbabel-comet
!pip install ast
!pip install bert-score git+https://github.com/huggingface/evaluate@af3c30561d840b83e54fc5f7150ea58046d6af69
!pip install bert-score
!pip install git+https://github.com/google-research/bleurt.git
!pip install nltk

# Import all this required libraries
from bert_score import score
import ast
from comet import download_model, load_from_checkpoint
from evaluate import load
import evaluate
import nltk
from nltk.tokenize import word_tokenize
import json

  Using cached AST-0.0.2.tar.gz (19 kB)
  error: subprocess-exited-with-error
  
  × python setup.py egg_info did not run successfully.
  │ exit code: 1
  ╰─> See above for output.
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
  Preparing metadata (setup.py) ... error
error: metadata-generation-failed

× Encountered error while generating package metadata.
╰─> See above for output.

note: This is an issue with the package mentioned above, not pip.
hint: See above for details.
  Cloning https://github.com/huggingface/evaluate (to revision af3c30561d840b83e54fc5f7150ea58046d6af69) to /tmp/pip-req-build-khi857qr
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/evaluate /tmp/pip-req-build-khi857qr
  Running command git rev-parse -q --verify 'sha^af3c30561d840b83e54fc5f7150ea58046d6af69'
  Running command git fetch -q https://github.com/huggingface/evaluate af3c30561d840b83e54fc5f7150ea58046d6af69
  Resolved ht

In [3]:
# Retrieve the python dictionary
data = []
with open("azure_dict.txt", "r", encoding='utf-8') as file:
    for line in file:
        dictionary_str = line.strip()
        entry = ast.literal_eval(dictionary_str)
        data.append(entry)

### COMET-22 METRIC

In [3]:
model_path = download_model("Unbabel/wmt22-comet-da")
model = load_from_checkpoint(model_path)
model_output = model.predict(data, batch_size=8, gpus=1)
print(model_output)
print(model_output[1])

Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.migration.utils:Lightning automatically upgraded your loaded checkpoint from v1.8.3.post1 to v1.9.5. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint --file ../root/.cache/huggingface/hub/models--Unbabel--wmt22-comet-da/snapshots/371e9839ca4e213dde891b066cf3080f75ec7e72/checkpoints/model.ckpt`


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting DataLoader 0: 100%|██████████| 12500/12500 [47:30<00:00,  4.39it/s]


Prediction([('scores', [0.9678432941436768, 0.8600401282310486, 0.9744556546211243, 0.9916894435882568, 0.8713392615318298, 0.6116134524345398, 0.9862480759620667, 0.8745012879371643, 0.9738827347755432, 0.8745011687278748, 0.9778863191604614, 0.8518990874290466, 0.8028380274772644, 0.842507004737854, 0.9025489091873169, 0.90821772813797, 0.8745012879371643, 0.9367218613624573, 0.8518990874290466, 0.8028379082679749, 0.9351786375045776, 0.8634635806083679, 0.8648726940155029, 0.9727665781974792, 0.8597244620323181, 0.9191785454750061, 0.9331256151199341, 0.8479982614517212, 0.9758816957473755, 0.8367132544517517, 0.8492061495780945, 0.9413890838623047, 0.8662508130073547, 0.8677136301994324, 0.8455150723457336, 0.9336053729057312, 0.9069409966468811, 0.8864961862564087, 0.8369389176368713, 0.9448969960212708, 0.9068490862846375, 0.8472804427146912, 0.7962477207183838, 0.9392343163490295, 0.9619418382644653, 0.8620668053627014, 0.942835807800293, 0.8094832301139832, 0.903574526309967, 0

In [4]:
azure_score = model_output[0]
azure_score.append(model_output[1])

with open("azure_comet22.txt", "w") as file:
    for number in azure_score:
        file.write(str(number) + "\n")

#with open("azure_comet22.txt", "r") as file:
#    numbers = [int(line.strip()) for line in file.readlines()]

In [4]:
# Since we no longer need the source sentences, we can just get a list with the predictions/hypothesis and a list with the references

predictions = [dictio['mt'] for dictio in data]
references = [dictio['ref'] for dictio in data]

## BERTScore METRIC

In [ ]:
bertscore = load("bertscore")
bert_output = bertscore.compute(predictions=predictions, references=references, lang="en")
print('Precision: ', sum(bert_output['precision'])/len(bert_output['precision']))
print('Recall: ', sum(bert_output['recall'])/len(bert_output['recall']))
print('F1: ', sum(bert_output['f1'])/len(bert_output['f1']))

In [ ]:
azure_bert_score = bert_output['precision']
azure_bert_score.append(sum(azure_bert_score)/len(azure_bert_score))

azure_bert_recall = bert_output['recall']
azure_bert_recall.append(sum(azure_bert_recall)/len(azure_bert_recall))

azure_bert_f1 = bert_output['f1']
azure_bert_f1.append(sum(azure_bert_f1)/len(azure_bert_f1))

with open("azure_bert_score.txt", "w") as file:
    for number in azure_bert_score:
        file.write(str(number) + "\n")

with open("azure_bert_recall.txt", "w") as file:
    for number in azure_bert_recall:
        file.write(str(number) + "\n")

with open("azure_bert_f1.txt", "w") as file:
    for number in azure_bert_f1:
        file.write(str(number) + "\n")

In [ ]:
# Second implementation (lower batch sizes)
rom bert_score import score
import numpy as np

batch_size = 100  # Number of pairs to process in each batch
# Calculate the total number of batches
num_batches = int(np.ceil(len(predictions) / batch_size))

# Compute BERTScore batch-wise
avg_P, avg_R, avg_F1 = 0, 0, 0
for batch_idx in range(num_batches):
    start_idx = batch_idx * batch_size
    end_idx = min((batch_idx + 1) * batch_size, len(predictions))

    # Extract batch of candidates and references
    batch_candidates = predictions[start_idx:end_idx]
    batch_references = references[start_idx:end_idx]

    # Compute BERTScore for the batch
    P, R, F1 = score(batch_candidates, batch_references, lang='en', verbose=True)

    # Accumulate the scores
    avg_P += P.sum().item()
    avg_R += R.sum().item()
    avg_F1 += F1.sum().item()

    print("Batch ", batch_idx, 'from ', num_batches, "P,R,F1:", avg_P,avg_R,avg_F1)

# Calculate the average scores
avg_P /= len(predictions)
avg_R /= len(predictions)
avg_F1 /= len(predictions)

# Print the average scores
print(f"Average Precision: {avg_P:.4f}")
print(f"Average Recall: {avg_R:.4f}")
print(f"Average F1-Score: {avg_F1:.4f}")

In [6]:
print(f"Average Precision: {avg_P:.4f}")
print(f"Average Recall: {avg_R:.4f}")
print(f"Average F1-Score: {avg_F1:.4f}")

Average Precision: 0.9580
Average Recall: 0.9560
Average F1-Score: 0.9569


In [7]:
with open("azure_bert_score.txt", "w") as file:
        file.write(str(avg_P) + "\n")

with open("azure_bert_recall.txt", "w") as file:
        file.write(str(avg_R) + "\n")

with open("azure_bert_f1.txt", "w") as file:
        file.write(str(avg_F1) + "\n")

### BLEURT METRIC

In [6]:
bleurt = load("bleurt", module_type="metric", checkpoint="BLEURT-20")
bleurt_output = bleurt.compute(predictions=predictions, references=references)

azure_bleurt_score = bleurt_output['scores']
means = sum(azure_bleurt_score)/len(azure_bleurt_score)
azure_bleurt_score.append(means)
print(means)    # from -infty to +infty

0.4297067375788838


In [7]:
with open("azure_bleurt.txt", "w") as file:
    for number in azure_bleurt_score:
        file.write(str(number) + "\n")

### METEOR METRIC

In [8]:
meteor = evaluate.load('meteor')
meteor_output = meteor.compute(predictions=predictions, references=references)
azure_meteor_score = meteor_output['meteor']
print(azure_meteor_score)

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


0.7239751162606427


In [9]:
# Second version (PRETOKENIZED)
# Tokenize predictions
tokenized_predictions = [word_tokenize(pred) for pred in predictions]
# Join tokenized predictions
joined_predictions = [" ".join(tokens) for tokens in tokenized_predictions]

# Tokenize references
tokenized_references = [word_tokenize(ref) for ref in references]
# Join tokenized references
joined_references = [" ".join(tokens) for tokens in tokenized_references]

#meteor = evaluate.load('meteor')
meteor_output_tokenizedstrat = meteor.compute(predictions=joined_predictions, references=joined_references)

azure_meteor_scorev2 = meteor_output_tokenizedstrat['meteor']
print(azure_meteor_scorev2)

0.7240093545345836


In [10]:
with open("azure_meteor.txt", "w") as file:
    for number in [azure_meteor_score]:
        file.write(str(number) + "\n")

### chrF(++) metrics

In [11]:
stacked_references = [[ref] for ref in references]  # We need to stack the references in lists although we don't have more than one per hypothesis
chrf = evaluate.load("chrf")
chrf_output = chrf.compute(predictions=predictions, references=stacked_references)
print(chrf_output) #from 0 to 100

{'score': 69.56775924113536, 'char_order': 6, 'word_order': 0, 'beta': 2}


In [12]:
chrf_output_pp = chrf.compute(predictions=predictions, references=stacked_references, word_order=2)
print(chrf_output_pp) #from 0 to 100

{'score': 67.4883424529703, 'char_order': 6, 'word_order': 2, 'beta': 2}


In [13]:
# Save the dictionaries to text files

with open('azure_chrf.txt', 'w') as file:
    json.dump(chrf_output, file)

with open('azure_chrf_pp.txt', 'w') as file:
    json.dump(chrf_output_pp, file)

# Load the dictionaries from the text files
#with open('flant5_chrf.txt', 'r') as file:
#    loaded_data = json.load(file)
# ...

### BLEU METRIC

In [14]:
bleu = evaluate.load("bleu")
bleu_output = bleu.compute(predictions=predictions, references=stacked_references)
print(bleu_output)

{'bleu': 0.4694362801113346, 'precisions': [0.7184493933007133, 0.5184587783863365, 0.40347473104360065, 0.3231319099899125], 'brevity_penalty': 1.0, 'length_ratio': 1.015607172625186, 'translation_length': 2629474, 'reference_length': 2589066}


In [15]:
# Initialize NLTK's word tokenizer
nltk.download('punkt')  # Download necessary resources for tokenization

# Tokenize the sentences into words and lowercase them
ntokenized_predictions = [word_tokenize(sentence.lower()) for sentence in predictions]
ntokenized_references = [word_tokenize(sentence.lower()) for sentence in references]

# Join the tokens of each sentence back into a string
njoined_predictions = [" ".join(tokens) for tokens in ntokenized_predictions]
njoined_references = [" ".join(tokens) for tokens in ntokenized_references]

nstacked_references = [[ref] for ref in njoined_references]

bleu_outputv2 = bleu.compute(predictions=njoined_predictions, references=nstacked_references)
print(bleu_outputv2)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


{'bleu': 0.4840472395612334, 'precisions': [0.7344065269381104, 0.5342791429437646, 0.41700865217188426, 0.33550668393753674], 'brevity_penalty': 1.0, 'length_ratio': 1.013768516174564, 'translation_length': 2643077, 'reference_length': 2607180}


In [16]:
with open('azure_bleu.txt', 'w') as file:
    json.dump(bleu_outputv2, file)

In [17]:
bleu_outputv3 = bleu.compute(predictions=njoined_predictions, references=nstacked_references, max_order=2)
print(bleu_outputv3)

## Of course, the results with this little max_order are way better but such little context makes no sense

{'bleu': 0.6264009018071417, 'precisions': [0.7344065269381104, 0.5342791429437646], 'brevity_penalty': 1.0, 'length_ratio': 1.013768516174564, 'translation_length': 2643077, 'reference_length': 2607180}
